In [1]:
!ls /kaggle/input/yolov3dataset
!ls /kaggle/working/checkpoints2025
!ls /kaggle/working/yolov3

checkpoints2025      LE_cand1	LEs576_new  yolov3
LE_ATLAS_tiles_cls3  LEs576aug	log_df
ls: cannot access '/kaggle/working/checkpoints2025': No such file or directory
ls: cannot access '/kaggle/working/yolov3': No such file or directory


In [2]:
!cp -r /kaggle/input/yolov3dataset/LE_cand1/LE_cand1 /kaggle/working/
!cp -r /kaggle/input/yolov3dataset/LE_ATLAS_tiles_cls3/LE_ATLAS_tiles_cls3 /kaggle/working/
#!cp -r /kaggle/input/yolov3dataset/LEs576_new/LEs576_new /kaggle/working/
#!cp -r /kaggle/input/yolov3dataset/LEs576aug/LEs576aug /kaggle/working/
!cp -r /kaggle/input/yolov3dataset/yolov3/yolov3 /kaggle/working/
!cp -r /kaggle/input/yolov3-detect-dataset/checkpoints_detect /kaggle/working/
!cp -r /kaggle/input/yolov3-detect-dataset/detect_df /kaggle/working/

In [3]:
#!cp -r /kaggle/input/yolov3dataset/dataset/dataset /kaggle/working/
#!cp -r /kaggle/input/yolov3dataset/LE_cand1/LE_cand1 /kaggle/working/
#!cp -r /kaggle/input/yolov3dataset/yolov3/yolov3 /kaggle/working/

In [4]:
#!cp -r /kaggle/input/yolov3dataset/yolov3/yolov3.py /kaggle/working/yolov3

In [5]:
#!rm -rf /kaggle/working/yolov3
#!rm -rf /kaggle/working/yolov3/yolov3.py

In [6]:
import os
import glob
import cv2
import numpy as np
import pandas as pd
import matplotlib
import matplotlib.pyplot as plt
%matplotlib inline  
import tensorflow as tf
from yolov3.yolov3 import Create_Yolov3
#from yolov3.utils import load_yolo_weights, detect_image
#from yolov3.configs import *

#input_size = YOLO_INPUT_SIZE
#Darknet_weights = YOLO_DARKNET_WEIGHTS

#yolo = Create_Yolov3(input_size=input_size)
#load_yolo_weights(yolo, Darknet_weights) # use Darknet weight

import torch

2025-05-21 13:53:58.247329: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1747835638.566858      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1747835638.618459      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [7]:
import colorsys
import random
def image_preprocess(image, target_size, gt_boxes=None):
    ih, iw    = target_size
    h,  w, _  = image.shape

    scale = min(iw/w, ih/h)
    nw, nh  = int(scale * w), int(scale * h)
    image_resized = cv2.resize(image, (nw, nh))

    image_paded = np.full(shape=[ih, iw, 3], fill_value=128.0)
    dw, dh = (iw - nw) // 2, (ih-nh) // 2
    image_paded[dh:nh+dh, dw:nw+dw, :] = image_resized
    image_paded = image_paded / 255.

    if gt_boxes is None:
        return image_paded

    else:
        gt_boxes[:, [0, 2]] = gt_boxes[:, [0, 2]] * scale + dw
        gt_boxes[:, [1, 3]] = gt_boxes[:, [1, 3]] * scale + dh
        return image_paded, gt_boxes


def postprocess_boxes(pred_bbox, original_image, input_size, score_threshold):
    valid_scale=[0, np.inf]
    pred_bbox = np.array(pred_bbox)

    pred_xywh = pred_bbox[:, 0:4]
    pred_conf = pred_bbox[:, 4]
    pred_prob = pred_bbox[:, 5:]

    # 1. (x, y, w, h) --> (xmin, ymin, xmax, ymax)
    pred_coor = np.concatenate([pred_xywh[:, :2] - pred_xywh[:, 2:] * 0.5,
                                pred_xywh[:, :2] + pred_xywh[:, 2:] * 0.5], axis=-1)
    # 2. (xmin, ymin, xmax, ymax) -> (xmin_org, ymin_org, xmax_org, ymax_org)
    org_h, org_w = original_image.shape[:2]
    resize_ratio = min(input_size / org_w, input_size / org_h)

    dw = (input_size - resize_ratio * org_w) / 2
    dh = (input_size - resize_ratio * org_h) / 2

    pred_coor[:, 0::2] = 1.0 * (pred_coor[:, 0::2] - dw) / resize_ratio
    pred_coor[:, 1::2] = 1.0 * (pred_coor[:, 1::2] - dh) / resize_ratio

    # 3. clip some boxes those are out of range
    pred_coor = np.concatenate([np.maximum(pred_coor[:, :2], [0, 0]),
                                np.minimum(pred_coor[:, 2:], [org_w - 1, org_h - 1])], axis=-1)
    invalid_mask = np.logical_or((pred_coor[:, 0] > pred_coor[:, 2]), (pred_coor[:, 1] > pred_coor[:, 3]))
    pred_coor[invalid_mask] = 0

    # 4. discard some invalid boxes
    bboxes_scale = np.sqrt(np.multiply.reduce(pred_coor[:, 2:4] - pred_coor[:, 0:2], axis=-1))
    scale_mask = np.logical_and((valid_scale[0] < bboxes_scale), (bboxes_scale < valid_scale[1]))

    # 5. discard boxes with low scores
    classes = np.argmax(pred_prob, axis=-1)
    scores = pred_conf * pred_prob[np.arange(len(pred_coor)), classes]
    score_mask = scores > score_threshold
    mask = np.logical_and(scale_mask, score_mask)
    coors, scores, classes = pred_coor[mask], scores[mask], classes[mask]

    return np.concatenate([coors, scores[:, np.newaxis], classes[:, np.newaxis]], axis=-1)

def nms(bboxes, iou_threshold, sigma=0.3, method='nms'):
    """
    :param bboxes: (xmin, ymin, xmax, ymax, score, class)

    Note: soft-nms, https://arxiv.org/pdf/1704.04503.pdf
          https://github.com/bharatsingh430/soft-nms
    """
    classes_in_img = list(set(bboxes[:, 5]))
    best_bboxes = []

    for cls in classes_in_img:
        cls_mask = (bboxes[:, 5] == cls)
        cls_bboxes = bboxes[cls_mask]
        # Process 1: Determine whether the number of bounding boxes is greater than 0 
        while len(cls_bboxes) > 0:
            # Process 2: Select the bounding box with the highest score according to socre order A
            max_ind = np.argmax(cls_bboxes[:, 4])
            best_bbox = cls_bboxes[max_ind]
            best_bboxes.append(best_bbox)
            cls_bboxes = np.concatenate([cls_bboxes[: max_ind], cls_bboxes[max_ind + 1:]])
            # Process 3: Calculate this bounding box A and
            # Remain all iou of the bounding box and remove those bounding boxes whose iou value is higher than the threshold 
            iou = bboxes_iou(best_bbox[np.newaxis, :4], cls_bboxes[:, :4])
            weight = np.ones((len(iou),), dtype=np.float32)

            assert method in ['nms', 'soft-nms']

            if method == 'nms':
                iou_mask = iou > iou_threshold
                weight[iou_mask] = 0.0

            if method == 'soft-nms':
                weight = np.exp(-(1.0 * iou ** 2 / sigma))

            cls_bboxes[:, 4] = cls_bboxes[:, 4] * weight
            score_mask = cls_bboxes[:, 4] > 0.
            cls_bboxes = cls_bboxes[score_mask]

    return best_bboxes

def draw_bbox(image, bboxes, CLASSES="./model_data/coco.names", show_label=True, show_confidence = True, Text_colors=(255,255,0), rectangle_colors=''):   
    NUM_CLASS = read_class_names(CLASSES)
    num_classes = len(NUM_CLASS)
    image_h, image_w, _ = image.shape
    hsv_tuples = [(1.0 * x / num_classes, 1., 1.) for x in range(num_classes)]
    #print("hsv_tuples", hsv_tuples)
    colors = list(map(lambda x: colorsys.hsv_to_rgb(*x), hsv_tuples))
    colors = list(map(lambda x: (int(x[0] * 255), int(x[1] * 255), int(x[2] * 255)), colors))

    random.seed(0)
    random.shuffle(colors)
    random.seed(None)

    for i, bbox in enumerate(bboxes):
        coor = np.array(bbox[:4], dtype=np.int32)
        score = bbox[4]
        class_ind = int(bbox[5])
        bbox_color = rectangle_colors if rectangle_colors != ''else colors[class_ind]
        #bbox_thick = int(0.6 * (image_h + image_w) / 1000) / 15  
        bbox_thick = int(0.6 * (image_h + image_w) / 500)
        #if bbox_thick < 1: bbox_thick = 1
        #print(image_h, image_w, bbox_thick)
        fontScale = 0.75 * bbox_thick
        (x1, y1), (x2, y2) = (coor[0], coor[1]), (coor[2], coor[3])

        # put object rectangle
        cv2.rectangle(image, (x1, y1), (x2, y2), bbox_color, bbox_thick*2)

        if show_label:
            # get text label
            #score_str = f' {score:.2f}' if show_confidence else ''
            score_str = " {:.2f}".format(score) if show_confidence else "" 
            #label = f'{NUM_CLASS[class_ind]}' + score_str
            label = "{}".format(NUM_CLASS[class_ind]) + score_str

            # get text size
            (text_width, text_height), baseline = cv2.getTextSize(label, cv2.FONT_HERSHEY_COMPLEX_SMALL,
                                                                  fontScale, thickness=bbox_thick)
            # put filled text rectangle
            cv2.rectangle(image, (x1, y1), (x1 + text_width, y1 - text_height - baseline), bbox_color, thickness=cv2.FILLED)

            # put text above rectangle
            cv2.putText(image, label, (x1, y1-4), cv2.FONT_HERSHEY_COMPLEX_SMALL,
                        fontScale, Text_colors, bbox_thick, lineType=cv2.LINE_AA)

    return image

def bboxes_iou(boxes1, boxes2):
    boxes1 = np.array(boxes1)
    boxes2 = np.array(boxes2)

    boxes1_area = (boxes1[..., 2] - boxes1[..., 0]) * (boxes1[..., 3] - boxes1[..., 1])
    boxes2_area = (boxes2[..., 2] - boxes2[..., 0]) * (boxes2[..., 3] - boxes2[..., 1])

    left_up       = np.maximum(boxes1[..., :2], boxes2[..., :2])
    right_down    = np.minimum(boxes1[..., 2:], boxes2[..., 2:])

    inter_section = np.maximum(right_down - left_up, 0.0)
    inter_area    = inter_section[..., 0] * inter_section[..., 1]
    union_area    = boxes1_area + boxes2_area - inter_area
    ious          = np.maximum(1.0 * inter_area / union_area, np.finfo(np.float32).eps)

    return ious

def read_class_names(class_file_name):
    # loads class name from a file
    names = {}
    with open(class_file_name, 'r') as data:
        for ID, name in enumerate(data):
            names[ID] = name.strip('\n')
    return names

In [8]:
def bbox_niou(boxes1, boxes2):
    #print("compute bbox_iou")
    # box [x, y, w, h], x,y: center of box
    boxes1_area = boxes1[..., 2] * boxes1[..., 3]
    boxes2_area = boxes2[..., 2] * boxes2[..., 3]
    
    #[, 4]
    global Pred_xywh, Label_xywh, BOX1, BOX2
    Pred_xywh = boxes1
    Label_xywh = boxes2

    boxes1 = tf.concat([boxes1[..., :2] - boxes1[..., 2:] * 0.5,
                        boxes1[..., :2] + boxes1[..., 2:] * 0.5], axis=-1)
    boxes2 = tf.concat([boxes2[..., :2] - boxes2[..., 2:] * 0.5,
                        boxes2[..., :2] + boxes2[..., 2:] * 0.5], axis=-1) 

    # output 
    BOX1 = boxes1
    BOX2 = boxes2
    print('boxes1',  boxes1.shape)
    print('boxes2', boxes2.shape)

    left_up = tf.maximum(boxes1[..., :2], boxes2[..., :2])
    right_down = tf.minimum(boxes1[..., 2:], boxes2[..., 2:])

    inter_section = tf.maximum(right_down - left_up, 0.0)
    inter_area = inter_section[..., 0] * inter_section[..., 1]
    union_area = boxes1_area + boxes2_area - inter_area

    iou = 1.0 * inter_area / union_area
    # add N_corner term
    # boxes2 contains boxes1 
    idx_4corners_2in1 = ( boxes1[..., 0] > boxes2[..., 0] ) & ( boxes1[..., 3] < boxes2[..., 3] ) \
                & ( boxes1[..., 1] > boxes2[..., 1]) & ( boxes1[..., 2] < boxes2[..., 2] )

    print("compute niou")
    #return 1.0 * inter_area / union_area
    #return iou + tf.cast( idx_4corners_2in1, tf.float32 )
    # change iou value to 1 if label contains pred
    idx_float = tf.cast( idx_4corners_2in1, tf.float32 )
    niou = iou * ( 1 - idx_float ) + idx_float
    return niou

In [9]:
def fits_to_uint8(fitsarr, vmin=-1, vmax=1,):
    
    # clip
    data = np.clip(fitsarr, vmin, vmax)
    # scale to [0,1]
    data = (data - vmin) / (vmax - vmin)
    # convert to uint8
    data = (255 * data).astype(np.uint8)
    # invert y axis
    #data = data[::-1, :]
    return data

def detect_(yolo, image_path = "./star/0.jpg", score_th=0.5, iou_nms=0.45, 
            showimg=False, readfits=False, clipfits=False, clipvmax=10, normfits=True, range01=True, showclassid=None):
    
    if readfits:
        fitspath = image_path.replace("jpg", "fits.npz")
        image_data = np.load(fitspath)["fitsarr"]
        #image_data_3d = np.dstack((image_data, image_data, image_data))
        if clipfits:
            image_data = np.clip(image_data, a_min=-clipvmax, a_max=clipvmax)
        if normfits:
            image_data = (image_data - image_data.mean() ) / image_data.std()

        if range01:
            image_data = (image_data + clipvmax) / (clipvmax * 2) # change range to [0, 1]

        #print("detect "fitspath)
        original_image = fits_to_uint8(image_data, vmin=-1, vmax=1)
        
    else:
        original_image      = cv2.imread(image_path)
        #original_image      = cv2.cvtColor(original_image, cv2.COLOR_BGR2RGB)    
        image_data = image_preprocess(np.copy(original_image), [input_size, input_size])

    image_data = tf.expand_dims(image_data, 0)
    
    pred_bbox = yolo.predict(image_data)
    pred_bbox = [tf.reshape(x, (-1, tf.shape(x)[-1])) for x in pred_bbox]
    pred_bbox = tf.concat(pred_bbox, axis=0)
        
    #bboxes = postprocess_boxes(pred_bbox, original_image, input_size, score_threshold=score_th)
    bboxes = postprocess_boxes(pred_bbox, original_image, input_size, score_threshold=score_th)
    bboxes = nms(bboxes, iou_threshold=iou_nms, method='nms')
    if showclassid!=None:
        stacked_bboxes = np.stack(bboxes, axis=0)
    
        # draw only bboxes of classid 
        bboxes = stacked_bboxes [stacked_bboxes[:, 5] == showclassid, :]
    
    image = draw_bbox(original_image, bboxes, CLASSES=TRAIN_CLASSES, 
                      Text_colors=(255,0,0),
                      rectangle_colors=(128,255,0))
    
    if showimg:
        plt.figure(figsize=(8, 8))
        plt.imshow(image)
    return np.array(bboxes)

In [10]:
def get_annot( annot_path = 'dataset/LEs920/train.txt'):
    """get annotation from dataset text"""
    with open(annot_path, 'r') as f:
        txt = f.readlines()
        annotations = [line.strip() for line in txt if len(line.strip().split()[1:]) != 0]
    resdic = {}
    for ann in annotations:
        ann = ann.split(' ')
        image_path = ann[0]
        boxarr = []
        for a in ann[1:]:
            box = np.fromstring(a, sep=',')
            boxarr.append(box)
        boxarr = np.array(boxarr)
        resdic[image_path] = boxarr

    return resdic

# plot predicted bbox

In [11]:
# #anntxt = "./dataset/LEs576/train.txt"
# #anntxt = "dataset/LEs576aug/train_aug1_s.txt"
# #anntxt = "dataset/LEs576_new/tiles/train_augs.txt"
# anntxt = "dataset/LEs576_new/tiles/test_augs.txt"

# anndic = get_annot(anntxt)
# imgfiles = list( anndic.keys() )

In [12]:
# train_imgs = [os.path.basename(i) for i in imgfiles]

In [13]:
# imgfiles

In [14]:
# import glob

# tileslist = glob.glob( './dataset/LEs576/tiles/*.jpg' )
# tileslist.sort()

In [15]:
# tileslist

In [16]:
# #bboxes_pred = detect_(yolo, image_path='./dataset/LEs576aug/tiles/.jpg', readfits=True,
# #                score_th=0.5, iou_nms=0.5, showimg=True)
# bboxes_list = []
# for imgfile in tileslist:
#     bboxes_pred = detect_(yolo, image_path=imgfile, readfits=True, showclassid=None,
#                 score_th=0.2, iou_nms=0.5, showimg=False)
    
#     bboxes_list.append(bboxes_pred)

In [17]:
# tileslist[0:9]

In [18]:
# image_path

In [19]:
# imgid = 8
# l = int( (imgid-1)*9)
# r = int(l+9)
# imgtiles = tileslist[l:r]
# box_tiles = bboxes_list[l:r]

# showclass = 0

# fig, axs = plt.subplots(3, 3, figsize=(10, 10), 
#                         gridspec_kw={'wspace':0.01, 'hspace':0.01}, )
# axs = axs.flatten()

# for i, image_path in enumerate(imgtiles):
#     ax = axs[i]
#     #ax.imshow(imgtile)
#     ax.axis('off')
#     ax.set_title(i)
#     fitspath = image_path.replace("jpg", "fits.npz")
#     image_data = np.load(fitspath)["fitsarr"]
#     rgb_img = fits_to_uint8(image_data, vmin=-1, vmax=1)
    
#     bboxes = box_tiles[i]
#     if len(bboxes)!=0:
#         if showclass!=None:
#             #stacked_bboxes = np.stack(bboxes, axis=0)

#             # draw only bboxes of classid 
#             bboxes = bboxes [bboxes[:, 5] == showclass, :]
#             labels = bboxes[:, 4]
#         else:
#             labels = bboxes[:, 5]
    
#     plot_bboxes(img=rgb_img, bboxes=bboxes, labels=labels, ax=ax)
#     if os.path.basename(image_path) in train_imgs:
#         ax.legend("t" )

# fig.savefig('./dataset/pred/{}.jpg'.format(imgid) )

In [20]:
# bboxes_pred

# get df_pred

In [21]:
def switchxy(boxes):
    """switch the coord of bounding boxes
    bboxes: array, shape [N, 4]
    """
    boxes_new = np.zeros( boxes.shape )
    boxes_new[:, 0],  boxes_new[:, 1]= boxes[:, 1], boxes[:, 0]
    boxes_new[:, 2],  boxes_new[:, 3]= boxes[:, 3], boxes[:, 2]

    return boxes_new

In [22]:
def get_iou(box1, box2):
    """ calculate intersection over union"""
    xi1 = max(box1[0], box2[0])
    yi1 = max(box1[1], box2[1])
    xi2 = min(box1[2], box2[2])
    yi2 = min(box1[3], box2[3])
    inter_area = max(yi2-yi1, 0) * max(xi2-xi1, 0)
    ### END CODE HERE ###    

    # Calculate the Union area by using Formula: Union(A,B) = A + B - Inter(A,B)
    ### START CODE HERE ### (≈ 3 lines)
    box1_area = (box1[3] - box1[1]) *  (box1[2] - box1[0])
    box2_area = (box2[3] - box2[1]) *  (box2[2] - box2[0])
    union_area = box1_area + box2_area - inter_area
    ### END CODE HERE ###
    
    # compute the IoU
    ### START CODE HERE ### (≈ 1 line)
    iou = inter_area / union_area
    ### END CODE HERE ###
    
    return iou

In [23]:
def get_giou(boxp, boxg, output='niou'):
    """ calculate generalized intersection over union
        boxp: predicted boxes
        boxg: groundtruth boxex
    """

    xp1, yp1, xp2, yp2 = boxp[0], boxp[1], boxp[2], boxp[3]
    xg1, yg1, xg2, yg2 = boxg[0], boxg[1], boxg[2], boxg[3]

    # calculate intersection
    xi1 = max(boxp[0], boxg[0])
    yi1 = max(boxp[1], boxg[1])
    xi2 = min(boxp[2], boxg[2])
    yi2 = min(boxp[3], boxg[3])
    inter_area = max(yi2-yi1, 0) * max(xi2-xi1, 0)

    # Calculate the Union area by using Formula: Union(A,B) = A + B - Inter(A,B)
    boxp_area = (boxp[3] - boxp[1]) *  (boxp[2] - boxp[0])
    boxg_area = (boxg[3] - boxg[1]) *  (boxg[2] - boxg[0])
    union_area = boxp_area + boxg_area - inter_area
    
    # finding the coordinate of smallest enclosing box
    xc1 = min(xp1, xg1)
    yc1 = min(yp1, yg1)
    xc2 = max(xp2, xg2)
    yc2 = max(yp2, yg2)
    
    # calculate area of enclosing box
    closing_area = (xc2 - xc1) * (yc2 - yc1)
    
    # compute the IoU gIoU
    iou = inter_area / union_area

    giou = iou - (closing_area - union_area) / closing_area

    # if boxp inside boxg
    boxes1 = boxp
    boxes2 = boxg
    idx_4corners_1in2 = ( boxes1[..., 0] > boxes2[..., 0] ) & ( boxes1[..., 3] < boxes2[..., 3] ) \
                & ( boxes1[..., 1] > boxes2[..., 1]) & ( boxes1[..., 2] < boxes2[..., 2] )
    niou = iou
    if idx_4corners_1in2:
        niou = 1

    if output=='iou':
        return iou
    elif output=='niou':
        #print('use niou')
        return niou
    elif output=='iop':
        return inter_area / boxp_area
    else:
        return giou

In [24]:
def bbox_iou_torch(box1, box2, x1y1x2y2=True, GIoU=False, DIoU=False, CIoU=False, mIoU=False, IoP=False, eps=1e-7):
    # Returns the IoU of box1 to box2. box1 is 4, box2 is nx4
    # bbox_iou(pred, target)
    
    box1 = box1.T
    box2 = box2.T

    # Get the coordinates of bounding boxes
    if x1y1x2y2:  # x1, y1, x2, y2 = box1
        b1_x1, b1_y1, b1_x2, b1_y2 = box1[0], box1[1], box1[2], box1[3]
        b2_x1, b2_y1, b2_x2, b2_y2 = box2[0], box2[1], box2[2], box2[3]
    else:  # transform from xywh to xyxy
        b1_x1, b1_x2 = box1[0] - box1[2] / 2, box1[0] + box1[2] / 2
        b1_y1, b1_y2 = box1[1] - box1[3] / 2, box1[1] + box1[3] / 2
        b2_x1, b2_x2 = box2[0] - box2[2] / 2, box2[0] + box2[2] / 2
        b2_y1, b2_y2 = box2[1] - box2[3] / 2, box2[1] + box2[3] / 2

    # Intersection area
    inter = (torch.min(b1_x2, b2_x2) - torch.max(b1_x1, b2_x1)).clamp(0) * \
            (torch.min(b1_y2, b2_y2) - torch.max(b1_y1, b2_y1)).clamp(0)

    # Union Area
    w1, h1 = b1_x2 - b1_x1, b1_y2 - b1_y1 + eps
    w2, h2 = b2_x2 - b2_x1, b2_y2 - b2_y1 + eps
    union = w1 * h1 + w2 * h2 - inter + eps

    #print(inter, union)
    #print('box1 shape', box1.shape, 'inter shape', inter.shape, )
    #print("compute IoU")
    iou = inter / union

    # -------------------------------
    # modified iou
    # if boxp inside boxg
    # boxes1 = boxp
    # boxes2 = boxg
    
    if mIoU:
        #print("compute mIoU")
        boxes1 = box1.T
        boxes2 = box2.T
        idx_4corners_1in2 = ( boxes1[..., 0] >= boxes2[..., 0] ) & ( boxes1[..., 3] <= boxes2[..., 3] ) \
                    & ( boxes1[..., 1] >= boxes2[..., 1]) & ( boxes1[..., 2] <= boxes2[..., 2] )
        #print(idx_4corners_1in2)
        #niou = iou
        iou[ idx_4corners_1in2] = 1
        #if idx_4corners_1in2:
        #  niou = 1
        
    if IoP:
        #print("compute IoP")
        iou = inter / (w1*h1)

    # -------------------------------

    if CIoU or DIoU or GIoU:
        cw = torch.max(b1_x2, b2_x2) - torch.min(b1_x1, b2_x1)  # convex (smallest enclosing box) width
        ch = torch.max(b1_y2, b2_y2) - torch.min(b1_y1, b2_y1)  # convex height
        if CIoU or DIoU:  # Distance or Complete IoU https://arxiv.org/abs/1911.08287v1
            c2 = cw ** 2 + ch ** 2 + eps  # convex diagonal squared
            rho2 = ((b2_x1 + b2_x2 - b1_x1 - b1_x2) ** 2 +
                    (b2_y1 + b2_y2 - b1_y1 - b1_y2) ** 2) / 4  # center distance squared
            if CIoU:  # https://github.com/Zzh-tju/DIoU-SSD-pytorch/blob/master/utils/box/box_utils.py#L47

                
                v = (4 / np.pi ** 2) * torch.pow(torch.atan(w2 / h2) - torch.atan(w1 / h1), 2)
                with torch.no_grad():
                    alpha = v / (v - iou + (1 + eps))
                print("compute CIoU")
                return iou - (rho2 / c2 + v * alpha)  # CIoU
            #print("compute DIoU")
            return iou - rho2 / c2  # DIoU
        c_area = cw * ch + eps  # convex area
        #print("compute GIoU")
        return iou - (c_area - union) / c_area  # GIoU https://arxiv.org/pdf/1902.09630.pdf
    
    return iou  # IoU

In [25]:
def get_df_pred(yolo, imgfiles, classids=[0, 1], readfits=True, clipfits=True, clipvmax=10, normfits=True, range01=False):
    """get predicted boxes for each file"""
    df_pred = pd.DataFrame(columns=['imgid', 'img', 'classid',
                                     'boxes_ann', 'label_ann',
                                     'boxes_pred', 'label_pred', 'score_pred'])

    #classids = [0, 1]
    for imgid, image_path in enumerate( imgfiles ):
        # get labeled boxes
        ann = anndic[image_path]
        boxes_ann = ann[:, :4]
        label_ann = ann[:, 4]
        #print(imgid, image_path)
        pred = detect_(yolo, image_path=image_path, readfits=readfits, clipfits=clipfits,
                                clipvmax=clipvmax, normfits=normfits, range01=range01,
                            score_th=0.0001, iou_nms=0.1, showimg=False) # score_th 0.0001

        if len(pred)==0:
            pred = np.array([ [0,0,0,0, 0, 0], [0,0,0,0, 0, 1], [0,0,0,0, 0, 2] ])
            print('empty prediction', imgid, image_path)

        # global PRED
        #PRED = pred
        #print(pred.shape)
        # pred for one img
        boxes_pred = pred[:, :4]
        score_pred = pred[:, 4]
        label_pred = pred[:, 5]

        for classid in classids:
            # prediction for one class
            cls_idx = label_pred == classid
            boxes_pred_cls = pred[:, :4] [cls_idx]
            score_pred_cls = pred[:, 4] [cls_idx]
            label_pred_cls = pred[:, 5] [cls_idx]

            # annotation for one class
            boxes_ann_cls = boxes_ann[label_ann==classid]
            label_ann_cls = label_ann[label_ann==classid]

            row = {'imgid':imgid, 'img': image_path, 'classid':classid,
                    'boxes_ann':boxes_ann_cls , 'label_ann': label_ann_cls,
                    'boxes_pred':boxes_pred_cls, 'label_pred':label_pred_cls, 'score_pred':score_pred_cls}
            df_pred.loc[len(df_pred.index)] = row
    return df_pred


In [26]:
def get_mat_iou_torch(df_pred, **kwargs):
    """ get the iou matrix between predicted and annotated box """

    boxp = df_pred['boxes_pred']
    boxa = df_pred['boxes_ann']
    
    boxa = torch.from_numpy(boxa, )

    # axis=0 pred; axis=1 ann
    gious = []  

    for bp in boxp:
        bp = torch.from_numpy(bp, )
        giou = bbox_iou_torch(bp, boxa, **kwargs) # giou(prediction, target)
        gious.append( giou.numpy()  )
    
    return np.array( gious )

In [27]:

def get_mat_iou(df_pred):
    """get the iou matrix between predicted and annotated box"""
    boxp = df_pred['boxes_pred']
    boxa = df_pred['boxes_ann']
    #  axis=0 pred; axis=1 ann
    matshape = ( boxp.shape[0], boxa.shape[0] )

    mat_iou = np.zeros( matshape )
    
    for i in range( matshape[0] ):
        for j in range( matshape[1] ):
            mat_iou[i, j] = get_giou(boxp=boxp[i], boxg=boxa[j], output='iou')
    return mat_iou

def get_mat_niou(df_pred):
    """get the iou matrix between predicted and annotated box"""
    boxp = df_pred['boxes_pred']
    boxa = df_pred['boxes_ann']
    #  axis=0 pred; axis=1 ann
    matshape = ( boxp.shape[0], boxa.shape[0] )

    mat_iou = np.zeros( matshape )
    
    for i in range( matshape[0] ):
        for j in range( matshape[1] ):
            mat_iou[i, j] = get_giou(boxp=boxp[i], boxg=boxa[j], output='niou')
    return mat_iou

def get_mat_iop(df_pred):
    """get the iou matrix between predicted and annotated box"""
    boxp = df_pred['boxes_pred']
    boxa = df_pred['boxes_ann']
    #  axis=0 pred; axis=1 ann
    matshape = ( boxp.shape[0], boxa.shape[0] )

    mat_iou = np.zeros( matshape )
    
    for i in range( matshape[0] ):
        for j in range( matshape[1] ):
            mat_iou[i, j] = get_giou(boxp=boxp[i], boxg=boxa[j], output='iop')
    return mat_iou

In [28]:
def get_iou_pred(df_pred):
    """get the max iou for each predicted box"""
    if df_pred['mat_iou'].shape[1]==0:
        ious = np.zeros( df_pred['mat_iou'].shape[0] )
    else:
        ious = np.max( df_pred['mat_iou'], axis=1)
    return ious

def get_objid_pred(df_pred):
    """get the object id for each predicted box"""
    if df_pred['mat_iou'].shape[1]==0:
        ious = np.zeros( df_pred['mat_iou'].shape[0] )
        objids = ious
        objids[ ious==0 ] = -1  # change to -1 if max iou =0
    else:
        ious = np.max( df_pred['mat_iou'], axis=1)
        objids = np.argmax( df_pred['mat_iou'], axis=1)
        objids = df_pred['imgid'] * 100 + objids
        objids[ ious==0 ] = -1  # change to -1 if max iou =0
    return objids

def get_iou_ann(df_pred):
    """get the max iou for each annotated box"""
    if 0 in df_pred['mat_iou'].shape:
        ious = np.array([])
    else:
        ious = np.max( df_pred['mat_iou'], axis=0)
    return ious

def get_score_ann(df_pred):
    """get the score for each annotated box"""
    if 0 in df_pred['mat_iou'].shape:
        score_ann = np.array([])
    else:
        ious = np.max( df_pred['mat_iou'], axis=0)
        predboxid = np.argmax( df_pred['mat_iou'], axis=0)
        score_ann = df_pred['score_pred'][ predboxid ]
        score_ann [ ious==0 ] = -1
    return score_ann

In [29]:
# get nTP
def get_nAnn(df_pred):
    """get number of Ann box"""
    nAnn = len( df_pred["label_ann"] )
    return nAnn

def get_nDet(df_pred, score_th=0.1):
    """get nDet for score > score_th"""
    nDet = np.sum( df_pred["score_pred"] > score_th )
    return nDet

def get_nTP_pred(df_pred, score_th=0.1, iou_th=0.1):
    
    ious_pred = df_pred['iou_pred']
    scores_pred = df_pred['score_pred']
    objids_pred = df_pred['objid_pred']

    ious_det_pred = ious_pred [ scores_pred > score_th ]
    #ious_det_ann = ious_ann [ scores_ann > score_th ]
    #objids_det = objids_pred[ scores_pred > score_th ]

    nTP_pred = np.sum( ious_det_pred > iou_th )
    return nTP_pred

def get_nTP_ann(df_pred, score_th=0.1, iou_th=0.1):
    
    ious_pred = df_pred['iou_pred']
    scores_pred = df_pred['score_pred']
    objids_pred = df_pred['objid_pred']

    ious_det_pred = ious_pred [ scores_pred > score_th ]
    #ious_det_ann = ious_ann [ scores_ann > score_th ]
    objids_det = objids_pred[ scores_pred > score_th ]

    #nTP_pred = np.sum( ious_det_pred > iou_th )
    objids_TP = objids_det[ ious_det_pred > iou_th ]
    #nTP_ann = np.sum( ious_det_ann > iou_th )
    nTP_ann = len( np.unique(objids_TP[objids_TP!=-1] ) )
    return nTP_ann

In [30]:
input_size = 576
TRAIN_CLASSES  = "/kaggle/working/LE_cand1/LEs_name2.txt" 
yolo = Create_Yolov3(input_size=input_size, CLASSES=TRAIN_CLASSES)


I0000 00:00:1747835657.206779      19 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 15513 MB memory:  -> device: 0, name: Tesla P100-PCIE-16GB, pci bus id: 0000:00:04.0, compute capability: 6.0
/usr/local/lib/python3.11/dist-packages/keras/src/layers/activations/leaky_relu.py:41: UserWarning: Argument `alpha` is deprecated. Use `negative_slope` instead.
  warnings.warn(


In [31]:
#change the path in the test_aug.txt
import os
input_file = "/kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt" 
output_file = "/kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt"  

with open(input_file, "r") as f:
    content = f.read()

new_content = content.replace(
    "./dataset/LE_cand1_cls3/tiles_aug/", 
    "/kaggle/working/LE_ATLAS_tiles_cls3/tiles_aug/"  
)

with open(output_file, "w") as f:
    f.write(new_content)

print(f"✅ save to: {output_file}")

✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt


In [32]:
anndic = get_annot("/kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt") 

imgfiles = list( anndic.keys() )

In [33]:
len(imgfiles)

80

In [34]:
def get_pr(df, classid, score_th = 0.2, iou_th = 0):
    """return precision and recall"""
    df = df[df.classid==classid].sort_values(by='img', inplace=False, ignore_index=True)
    df[f'nDet_s{score_th}'] = df.apply(get_nDet, args=(score_th,), axis=1, )
    df[f'nTP_pred_s{score_th}_i{iou_th}'] = df.apply(get_nTP_pred, args=(score_th, iou_th), axis=1, )
    df[f'nTP_ann_s{score_th}_i{iou_th}'] = df.apply(get_nTP_ann, args=(score_th, iou_th), axis=1, )

    nTP_pred = df[f'nTP_pred_s{score_th}_i{iou_th}'].sum()
    nTP_ann = df[f'nTP_ann_s{score_th}_i{iou_th}'].sum()
    nDet = df[f'nDet_s{score_th}'].sum()
    nAnn = df[f'nAnn'].sum()

    p = nTP_pred / nDet
    r = nTP_ann / nAnn

    return p, r

In [35]:
for epoch in range(2, 101, 2): print(epoch)

2
4
6
8
10
12
14
16
18
20
22
24
26
28
30
32
34
36
38
40
42
44
46
48
50
52
54
56
58
60
62
64
66
68
70
72
74
76
78
80
82
84
86
88
90
92
94
96
98
100


In [36]:
for run in [7, 8, 9, 10, 11, 12]:
    import os
    input_file = f"/kaggle/working/LE_ATLAS_tiles_cls3/test_aug{run}.txt" 
    output_file = f"/kaggle/working/LE_ATLAS_tiles_cls3/test_aug{run}.txt"  

    with open(input_file, "r") as f:
        content = f.read()

    new_content = content.replace(
        "./dataset/LE_cand1_cls3/tiles_aug", 
        "/kaggle/working/LE_ATLAS_tiles_cls3/tiles_aug/"  
    )

    with open(output_file, "w") as f:
        f.write(new_content)
    print(f"✅ save to: {output_file}")

✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt
✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug8.txt
✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug9.txt
✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug10.txt
✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug11.txt
✅ save to: /kaggle/working/LE_ATLAS_tiles_cls3/test_aug12.txt


In [37]:
%%time
#for modelname in  ['model_miou_v1', 'model_niou_v2','model_iou_v3']:
#for modelname in  ['model_iou_v2', 'model_miou_v3']:

#modelname = 'model_miou_v1'
#modelname = 'model_miou_v4'
# epoch = 50

#for modelname in [ 'model_miou_train_aug8', 'model_miou_train_aug9',]:#'model_miou_train_aug2_range01', 'model_miou_train_aug3_range01', ]: #'model_iou_v2',
#                   #'model_miou_v3' , 'model_miou_v4', 'model_iop_v5']:

for run in [7, 8, 9, 10, 11, 12]:
#for run in [7]:
    
    testpath = f"/kaggle/working/LE_ATLAS_tiles_cls3/test_aug{run}.txt"
    modelname = f"model_miou_train_aug1"

    print(modelname, testpath)
    anndic = get_annot(testpath)
    imgfiles = list( anndic.keys() )

    for epoch in range(0, 61, 5):
    #for epoch in [10]: 
        weights = f"{modelname}_ep{epoch}.weights.h5"
        print("load weights ", weights)

        yolo.load_weights(f"/kaggle/working/checkpoints_detect/run1/{weights}")
        loaded_layers = [l for l in yolo.layers if l.weights]
        print(f"successfully loaded {len(loaded_layers)}/{len(yolo.layers)} ")

        tf.config.run_functions_eagerly(True) 

        #print("getting df_pred... ")
        #if 'v3' in modelname:
        #    df_pred = get_df_pred(yolo, imgfiles, clipvmax=1, normfits=True)
        #elif 'v4' in modelname:
        #    df_pred = get_df_pred(yolo, imgfiles, clipvmax=10, normfits=False)
        #elif 'v2' in modelname:
        #    df_pred = get_df_pred(yolo, imgfiles, clipvmax=10, normfits=False, range01=True)
        #    print('scale to [0, 1]')
        #else:
        df_pred = get_df_pred(yolo, imgfiles, classids=[0, 1, 2], clipvmax=10, normfits=True, range01=False)

        #df_pred_iou = df_pred.copy()
        df_pred_iop = df_pred.copy()

        print("computing iou...")
        df_pred['mat_iou'] = df_pred.apply(get_mat_niou, axis=1)
        #df_pred_iou['mat_iou'] = df_pred_iou.apply(get_mat_iou, axis=1)
        df_pred_iop['mat_iou'] = df_pred_iop.apply(get_mat_iop, axis=1)

        #for df in [df_pred, df_pred_iou, df_pred_iop]:
        for df in [df_pred, df_pred_iop]:

            df['iou_pred'] = df.apply(get_iou_pred , axis=1)
            df['objid_pred'] = df.apply(get_objid_pred , axis=1)
            df['iou_ann'] = df.apply(get_iou_ann , axis=1)
            df['score_ann'] = df.apply(get_score_ann , axis=1)

            # Ann
            df['nAnn'] = df.apply(get_nAnn, axis=1)
            df['nDet_s0.2'] = df.apply(get_nDet, args=(0.2,), axis=1, )
            df['nTP_pred_s0.2_i0.1'] = df.apply(get_nTP_pred, args=(0.2, 0.1), axis=1, )
            df['nTP_ann_s0.2_i0.1'] = df.apply(get_nTP_ann, args=(0.2, 0.1), axis=1, )

        print(f"{epoch} save to pickle")
        save_dir = f"/kaggle/working/detect_df/run{run}/"
        os.makedirs(save_dir, exist_ok=True) 
        df_pred.to_pickle(f"{save_dir}df_pred_miou_{weights}_testset_largebox.pickle")
        #df_pred_iou.to_pickle(f"./log_df/df_pred_iou_{weights}_testset_largebox.pickle")
        df_pred_iop.to_pickle(f"{save_dir}df_pred_iop_{weights}_testset_largebox.pickle")
        

model_miou_train_aug1 /kaggle/working/LE_ATLAS_tiles_cls3/test_aug7.txt
load weights  model_miou_train_aug1_ep0.weights.h5
successfully loaded 147/255 


/usr/local/lib/python3.11/dist-packages/tensorflow/python/data/ops/structured_function.py:258: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(
I0000 00:00:1747835659.734064      19 cuda_dnn.cc:529] Loaded cuDNN version 90300


1/1 ━━━━━━━━━━━━━━━━━━━━ 3s 3s/step


/usr/local/lib/python3.11/dist-packages/tensorflow/python/data/ops/structured_function.py:258: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 271ms/step


...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 279ms/step


/usr/local/lib/python3.11/dist-packages/tensorflow/python/data/ops/structured_function.py:258: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 272ms/step


/usr/local/lib/python3.11/dist-packages/tensorflow/python/data/ops/structured_function.py:258: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  warnings.warn(


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 276ms/step
computing iou...
60 save to pickle
CPU times: user 1h 27min 30s, sys: 1min 28s, total: 1h 28min 59s
Wall time: 1h 26min 33s


In [38]:
import shutil
import os
shutil.make_archive('/kaggle/working/detect_df', 'zip', "/kaggle/working/detect_df")

'/kaggle/working/detect_df.zip'

In [39]:
# import cv2
# image_path = "/kaggle/input/yolov3dataset/LE_ATLAS_tiles_cls3/LE_ATLAS_tiles_cls3/tiles/001_2.jpg"
# image = cv2.imread(image_path)
# print(image.shape)